In [2]:
import csv
import cv2
# import dlib
from ultralytics import YOLO
import os
import numpy as np
import tqdm
import pandas as pd
import pickle
import cv2
from tqdm import tqdm


In [ ]:
# Svhkpt wpckpn,'w'kumpds,
#FIEPTH:/://MPD/pyb

In [3]:
column_headings = ["image-Path", "YOlov8", "opencv", "dlib"]
with open('face_detection_results.csv', mode='a', newline='') as file:
    writer = csv.writer(file)
    # Write the column headings
    writer.writerow(column_headings)

In [1]:
import tkinter as tk
from PIL import Image, ImageTk
import pandas as pd

Model = 'YoloModel'
path = r'D:\Uni\FYP\test.csv'
savingTime = 2000

# Global variables to store image and photo references
img = None
photo = None

# Function to handle button clicks
def handle_click(row_index, result):
    global df, root, img_label

    if result == "FP":
        df.at[row_index, Model] = "FP"
    elif result == "FN":
        df.at[row_index, Model] = "FN"
    elif result == "Tn":
        df.at[row_index,Model] = "Tn"
    elif result == "Skip":
        df.at[row_index, Model] = "None"

    df = df.fillna("None")
    # Update the dataframe or do any other processing here

    # Destroy the current buttons and image
    for widget in root.winfo_children():
        widget.destroy()

    # Display the next image with 'No' value in the dataframe
    display_images()

# Function to save the DataFrame to CSV
def save_to_csv():
    global df, path
    df.to_csv(path, index=False)
    # Schedule the next autosave in 2 seconds
    root.after(savingTime, save_to_csv)

# Function to display images and buttons
def display_images():
    global df, root, img_label, img, photo

    # Filter rows with 'No' value in the specified model column
    no_rows = df[df[Model] == 'No']

    if not no_rows.empty:
        row = no_rows.iloc[0]  # Consider the first row with 'No' value
        row_number = row.name  # Get the row number

        img_path = row['imagepath']
        result = row[Model]

        # Update the window title with the image path and row number
        root.title(f"Image Review - Row: {row_number}, Image Path: {img_path}")
        print(img_path)

        # Display image using img_path and create buttons
        img = Image.open(img_path)
        img = img.resize((300, 300))  # Resize the image as needed
        photo = ImageTk.PhotoImage(img)
        img_label = tk.Label(root, image=photo)
        img_label.image = photo  # Keep a reference to avoid garbage collection
        img_label.pack()

        button_fp = tk.Button(root, text="Object detected as Face", command=lambda: handle_click(row_number, "FP"))
        button_fp.pack()

        button_fn = tk.Button(root, text="Face But No Face Detected", command=lambda: handle_click(row_number, "FN"))
        button_fn.pack()
        
        button_fn = tk.Button(root, text="Tn", command=lambda: handle_click(row_number, "Tn"))
        button_fn.pack()

        button_skip = tk.Button(root, text="Skip", command=lambda: handle_click(row_number, "Skip"))
        button_skip.pack()


    else:
        # If there are no more 'No' values, display a message or perform any other action
        print("No more images with 'No' values in specified column")

# Read the CSV file
df = pd.read_csv(path)

# Initialize Tkinter
root = tk.Tk()
root.title("Image Review")

# Start autosave loop
root.after(savingTime, save_to_csv)

# Start displaying images and buttons
display_images()

root.mainloop()


D:/Uni/FYP/results\20k0169\Beard_and_Glasses\down-to-up\1\yolo_0021_8.jpg
D:/Uni/FYP/results\20k0169\Beard_and_Glasses\down-to-up\1\yolo_0022_8.jpg


In [15]:
import pandas as pd

# Read the three CSV files
yolo_df = pd.read_csv(r'D:\Uni\FYP\final.csv')
opencv_df = pd.read_csv(r'D:\Uni\FYP\new-opencv-labels.csv')

# Make sure the column names are correctly referenced without spaces
yolo_df.rename(columns={'Yolo Model': 'Yolo_Model'}, inplace=True)
opencv_df.rename(columns={'OpenCv Model': 'OpenCv_Model'}, inplace=True)

# Extract filenames without the directory path
yolo_df['Filename'] = yolo_df['imagepath'].str.split('/').str[-1]
yolo_df['BasePath'] = yolo_df['Filename'].str.split('yolo').str[0]

opencv_df['Filename'] = opencv_df['imagepath'].str.split('/').str[-1]
opencv_df['BasePath'] = opencv_df['Filename'].str.split('opencv').str[0]

yolo_df['FrameNumber'] = yolo_df['Filename'].str.extract(r'yolo_(\d+)')
opencv_df['FrameNumber'] = opencv_df['Filename'].str.extract(r'opencv_(\d+)')

yolo_df['commonPath'] = yolo_df['BasePath'] + yolo_df['FrameNumber'] + '.jpg'
opencv_df['commonPath'] = opencv_df['BasePath'] + opencv_df['FrameNumber'] + '.jpg'


print("\nUpdated opencv_df:")
opencv_df.head()

# Create a new DataFrame by merging the common paths
merged_paths = pd.merge(yolo_df[['imagepath', 'commonPath', 'Yolo_Model']],
                        opencv_df[['imagepath', 'commonPath', 'OpenCv_Model']],
                        on='commonPath', how='inner')

# Rename columns in the new DataFrame
merged_paths.rename(columns={'imagepath_x': 'yolo_path', 'imagepath_y': 'opencv_path',
                             'Yolo_Model': 'yoloValue', 'OpenCv_Model': 'openCvValue'},
                    inplace=True)

merged_paths = merged_paths[['commonPath', 'yolo_path', 'opencv_path', 'yoloValue', 'openCvValue']]

# print(merged_df)
# # Replace 'frameNum' values in the respective columns
# merged_df['YoloModel'] = merged_df['YoloModel'].fillna(merged_df['YoloModel'].str.replace('yolo_frameNum_', ''))
# merged_df['OpenCvModel'] = merged_df['OpenCvModel'].fillna(merged_df['OpenCvModel'].str.replace('opencv_frameNum_', ''))

# # Display the merged dataframe


Updated opencv_df:


KeyError: "['OpenCv_Model'] not in index"

In [74]:
merged_paths.to_csv('merged_paths.csv', index=True)

In [ ]:
print(yolo_df['Filename'][0])
print(opencv_df['Filename'][0])


print(yolo_df)


In [13]:
import pandas as pd

# Read the merge.csv file into a Pandas DataFrame
merge_df = pd.read_csv('merged_paths.csv')

# Find duplicate values in the 'opencv_path' column
duplicate_opencv_paths = merge_df[merge_df.duplicated('opencv_path', keep=False)]
# 'keep=False' ensures that all instances of duplicates are marked as True

# Display duplicate values in the 'opencv_path' column
print("Duplicate opencv_path values:")
print(duplicate_opencv_paths['opencv_path'])

Duplicate opencv_path values:
636      D:/face_detection/MP_Data/results\20k0140\All\...
637      D:/face_detection/MP_Data/results\20k0140\All\...
1214     D:/face_detection/MP_Data/results\20k0145\Bear...
1215     D:/face_detection/MP_Data/results\20k0145\Bear...
2410     D:/face_detection/MP_Data/results\20k0169\Bear...
                               ...                        
14763    D:/face_detection/MP_Data/results\20k0308\Glas...
14934    D:/face_detection/MP_Data/results\20k0308\Glas...
14935    D:/face_detection/MP_Data/results\20k0308\Glas...
14936    D:/face_detection/MP_Data/results\20k0308\Glas...
14937    D:/face_detection/MP_Data/results\20k0308\Glas...
Name: opencv_path, Length: 363, dtype: object


In [10]:
import cv2

# Function to detect faces using YOLOv8 and extract the first detected face
def use_yolo(img_path):
    # Assume model_yolov8 is defined and loaded somewhere in your code
    model_yolov8=YOLO("./yolov8n-face.pt")
    results = model_yolov8(img_path)

    # Access bounding boxes directly (assuming YOLOv8 returns a list)
    faces = results[0].boxes

    if len(faces) > 0:
        x1, y1, x2, y2 = map(int, faces[0].xyxy[0].tolist())
        img = cv2.imread(img_path)
        
        confidence=faces.conf.tolist()[0]
        # print(confidence)
        # Draw a bounding box around the detected face
        cv2.rectangle(img, (x1, y1), (x2, y2), (0, 255, 0), 2)  # Green rectangle
        cv2.putText(img, f"Confidence: {confidence:.2f}", (x1, y1 - 5),cv2.FONT_HERSHEY_SIMPLEX, 0.5, (0, 255, 0), 2)

        return img 
    else:
        return None
    



def use_opencv(img_path):
    image = cv2.imread(img_path)
    gray = cv2.cvtColor(image, cv2.COLOR_BGR2GRAY)
    face_cascade = cv2.CascadeClassifier(cv2.data.haarcascades + './haarcascade_frontalface_default.xml')
    faces = face_cascade.detectMultiScale(gray, scaleFactor=1.1, minNeighbors=1, minSize=(30, 30),)




    if len(faces) > 0:
        # Draw bounding boxes for detected faces
        for (x, y, w, h) in faces:
            cv2.rectangle(image, (x, y), (x+w, y+h), (0, 255, 0), 2)
            # confidence = weights[-1]  
            # print(confidence)  # Green rectangle
            # cv2.putText(image, f"Confidence: {confidence:.2f}", (x, y - 5),
            # cv2.FONT_HERSHEY_SIMPLEX, 0.5, (0, 255, 0), 2)

        return image  # Return the image with bounding boxes
    else:
        return None 


def use_dlib(img_path): 
    image = cv2.imread(img_path)
    gray = cv2.cvtColor(image, cv2.COLOR_BGR2GRAY)
    detector = dlib.get_frontal_face_detector()
    dlib_faces = detector(gray)

    if len(dlib_faces) > 0:
        # Draw bounding boxes for detected faces
        for face in dlib_faces:
            x1 = face.left()
            y1 = face.top()
            x2 = face.right()
            y2 = face.bottom()
            cv2.rectangle(image, (x1, y1), (x2, y2), (0, 255, 0), 2)  # Green rectangle

        return image  # Return the image with bounding boxes
    else:
        return None

def save_cropped_faces(input_dir, output_directory,checkpoint_file="checkpoint_faces.pkl"):
    counter=0
    
    yolo_path='yolov8n-face.pt'
    model_yolov8= YOLO(yolo_path)

    processed_images = set()
    if os.path.exists(checkpoint_file):
        with open(checkpoint_file, 'rb') as f:
            processed_images = pickle.load(f)
            counter=len(processed_images)

            print("Loaded {} already processed images".format(len(processed_images)))
    # Process images recursively
    for root, _, files in os.walk(input_dir):

        # for img_file in tqdm(files, unit="image", leave=False):
            for file in files:
                img_path = os.path.join(root, file)

                # Relative path to the input directory
                relative_path = os.path.relpath(img_path, input_dir)
                # print(relative_path)
                # Skip if already processed

                
                if relative_path in processed_images:
                    continue

                yolo = use_yolo(img_path)
                if yolo is not None:
                    # Construct output directory structure
                    output_subdir = os.path.join(output_directory, os.path.dirname(relative_path))
                    os.makedirs(output_subdir, exist_ok=True)
                    output_path = os.path.join(output_subdir, f"yolo_{os.path.basename(relative_path)}")
                    cv2.imwrite(output_path, yolo)
                else:
                    original_path = os.path.join(output_subdir, f"yolo_{os.path.basename(relative_path)}")
                    image=cv2.imread(img_path)
                    cv2.imwrite(original_path, image)


                    
                # opencv = use_opencv(img_path)
                # if opencv is not None:
                #     # Construct output directory structure
                #     output_subdir = os.path.join(output_directory, os.path.dirname(relative_path))
                #     os.makedirs(output_subdir, exist_ok=True)
                #     output_path = os.path.join(output_subdir, f"opencv_{os.path.basename(relative_path)}")
                #     cv2.imwrite(output_path, opencv)
                # else:
                #     original_path = os.path.join(output_subdir, f"opencv_{os.path.basename(relative_path)}")
                #     image=cv2.imread(img_path)
                #     cv2.imwrite(original_path, image)



                # dlib = use_dlib(img_path)
                # if dlib is not None:
                #     # Construct output directory structure
                #     output_subdir = os.path.join(output_directory, os.path.dirname(relative_path))
                #     os.makedirs(output_subdir, exist_ok=True)
                #     output_path = os.path.join(output_subdir, f"dlib_{os.path.basename(relative_path)}")
                #     cv2.imwrite(output_path, dlib)
                # else:
                #     original_path = os.path.join(output_subdir, f"dlib_{os.path.basename(relative_path)}")
                #     image=cv2.imread(img_path)
                #     cv2.imwrite(original_path, image)


                    # Update processed images set
                processed_images.add(relative_path)

                    # Save checkpoint
                with open(checkpoint_file, 'wb') as f:
                    pickle.dump(processed_images, f)
                with open('face_detection_results.csv', mode='a',newline='') as file:
                    writer = csv.writer(file)
                    writer.writerow([relative_path])

                counter += 1
                print(counter)


In [11]:
input_directory = "input_images"
checkpoint_filename = "checkpoint_faces.pkl"
output_directory="results"

save_cropped_faces(input_directory, output_directory,checkpoint_filename)

WARNING ⚠️ yolov8n-face.pt appears to require 'omegaconf', which is not in ultralytics requirements.
AutoInstall will run now for 'omegaconf' but this feature will be removed in the future.
Recommend fixes are to train a new model using the latest 'ultralytics' package or to run a command with an official YOLOv8 model, i.e. 'yolo predict model=yolov8n.pt'
requirements: Ultralytics requirement ['omegaconf'] not found, attempting AutoUpdate...
     -------------------------------------- 79.5/79.5 kB 341.2 kB/s eta 0:00:00
     ------------------------------------ 117.0/117.0 kB 427.2 kB/s eta 0:00:00
  Preparing metadata (setup.py): started
  Preparing metadata (setup.py): finished with status 'done'
  Created wheel for antlr4-python3-runtime: filename=antlr4_python3_runtime-4.9.3-py3-none-any.whl size=144578 sha256=32e32240bd73ce28a9987d0f7efa23600eac815152026920490486529588750a
  Stored in directory: C:\Users\Mohsin\AppData\Local\Temp\pip-ephem-wheel-cache-gg4w254j\wheels\12\93\dd\1f6a

KeyboardInterrupt: 